In [0]:
df = spark.read.csv("/Volumes/workspace/ecommerce/ecommerce_data/2019-Nov.csv", header=True, inferSchema=True)
df.write.format("delta").mode("overwrite").save("/Volumes/workspace/ecommerce/ecommerce_data/2019-Nov-delta")

In [0]:
df.write.format("delta").mode("overwrite").saveAsTable("workspace.ecommerce.ecommerce_nov_2019_data")

In [0]:
spark.sql("""
CREATE TABLE workspace.ecommerce.ecommerce_nov_2019_data_sql
USING DELTA
AS
SELECT * FROM delta.`/Volumes/workspace/ecommerce/ecommerce_data/2019-Nov-delta`
""")

DataFrame[num_affected_rows: bigint, num_inserted_rows: bigint]

In [0]:
from pyspark.sql.types import StructType, StructField, IntegerType, StringType

# Define a schema with a type mismatch for an existing column (e.g., 'price' as Integer instead of original type)
schema = StructType([
    StructField("price", IntegerType(), True),
    StructField("product_id", StringType(), True),
    StructField("user_id", StringType(), True)
])

# Create a DataFrame with a row that violates the schema (e.g., 'price' as a string)
data = [("not_a_number", "P123", "U456")]
df_invalid = spark.createDataFrame(data, schema=schema)

# Attempt to write invalid data to the Delta table to test schema enforcement
try:
    df_invalid.write.format("delta").mode("append").saveAsTable("workspace.ecommerce.ecommerce_nov_2019_data")
except Exception as e:
    print("Schema enforcement error:", e)

---------------------------------------------------------------------------
ArrowInvalid                              Traceback (most recent call last)
File <command-8233440208701808>, line 12
     10 # Create a DataFrame with a row that violates the schema (e.g., 'price' as a string)
     11 data = [("not_a_number", "P123", "U456")]
---> 12 df_invalid = spark.createDataFrame(data, schema=schema)
     14 # Attempt to write invalid data to the Delta table to test schema enforcement
     15 try:

File /databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/session.py:813, in SparkSession.createDataFrame(self, data, schema, samplingRatio, verifySchema)
    806     from pyspark.sql.conversion import (
    807         LocalDataToArrowConversion,
    808     )
    810     # Spark Connect will try its best to build the Arrow table with the
    811     # inferred schema in the client side, and then rename the columns and
    812     # cast the datatypes in the server side.
--> 813 

In [0]:
from pyspark.sql import functions as F

# Remove duplicates based on unique columns before insert (e.g., 'product_id', 'user_id')
df_no_duplicates = df.dropDuplicates(["product_id", "user_id"])
display(df_no_duplicates.count())
df_no_duplicates.write.format("delta").mode("overwrite").saveAsTable("workspace.ecommerce.ecommerce_nov_2019_data")

34442983

In [0]:

from pyspark.sql import functions as F, Window

df_oct = spark.read.csv("/Volumes/workspace/ecommerce/ecommerce_data/2019-Oct.csv", header=True, inferSchema=True)

w = Window.partitionBy("product_id", "user_id").orderBy(F.col("event_time").desc())
df_ranked = df_oct.withColumn("rn", F.row_number().over(w))
dedup = df_ranked.filter(F.col("rn") == 1).drop("rn")
display(dedup)


event_time event_type product_id category_id category_code brand price user_id user_session 2019-10-30T06:37:16.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 512495920 6140ad98-e98a-4eb2-8d69-d5777b308550 2019-10-24T20:54:53.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 512599507 a1bc31d2-8225-4c3a-bd17-77970ea15a6d 2019-10-25T15:48:19.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 512885938 7d27b5b1-60c5-4b05-ae7d-8f25e639a76d 2019-10-22T07:48:13.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 300.91 513268031 600525e9-2a42-4e30-8b65-2ee2e625b1ea 2019-10-30T12:15:50.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 513273941 7b7aa0c3-89a3-4b61-a5db-2d1597555e88 2019-10-27T17:07:34.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 513428499 e7e3f9a8-baba-482d-a851-ce8a9f0f88cf 2019-10-25T09:01:13.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 513709431 4a1c6fd3-ad47-4a05-a25f-68812518164c 2019-10-31T12:52:00.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 513815785 34a4a0b7-3df2-4ee4-9681-f5df2acbdf0d 2019-10-29T11:39:55.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 514492080 ffc6fd9f-6980-4236-a9c2-6508a4fc0c70 2019-10-23T07:58:48.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 514544551 e8b53f5f-f857-4c87-945f-5931f1d35d4d 2019-10-26T16:45:48.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 514707151 ba60b4ac-87fc-4593-84e2-83f29cd9ccbc 2019-10-29T11:00:47.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 515062750 c083e10c-c45a-49ca-959b-305889731023 2019-10-26T15:23:04.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 515779823 eec98a79-54d0-4a15-9344-4d0f7ab09602 2019-10-29T12:54:12.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 515798088 764db36a-14df-4230-b62d-1b3b4e43bd38 2019-10-24T04:11:14.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 516430288 87284c1e-21e8-4085-a278-3956e2da04c7 2019-10-22T11:31:42.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 300.91 517035901 f3493241-4a66-4b17-92c2-d98495390473 2019-10-26T08:40:21.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 517123751 008bd148-aca6-4b64-aa75-f363813b796a 2019-10-30T12:13:03.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 517802289 72c2de61-96c1-4be9-9363-25a5a40a9d19 2019-10-29T18:52:27.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 518731154 fb6a3c3d-d129-4856-b6e0-75cce037d4ed 2019-10-24T19:12:28.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 520594568 dec10036-e8bc-421d-ac94-c2e645c64344 2019-10-22T16:50:14.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 300.91 522153982 44835e1b-b5ca-4630-b72d-90a73de0b78d 2019-10-27T16:17:28.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 522970808 86098b26-cd93-40bb-8a0a-8c9cb7a49875 2019-10-21T06:29:22.000Z view 1000978 2053013555631882655 electronics.smartphone null 0.0 525181011 91514c00-b4df-42a9-b803-7605be1da80c 2019-10-30T14:28:58.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 527349279 7fb3bc8a-04aa-4554-b437-db05aa035066 2019-10-29T15:38:03.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 301.14 528259434 144184ec-19ff-4e40-bd7c-f6f59a1199df 2019-10-23T17:47:01.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 529587549 03aeab53-d9f7-4170-b231-e2fd9bf5c8b0 2019-10-24T08:10:01.000Z view 1000978 2053013555631882655 electronics.smartphone samsung 333.49 529930508 c0a33743-85c0-41ae-88cf-e03c2e13aa5a 2019-10-22T15:13:11.000Z view 1000978 205301355563188

In [0]:
from pyspark.sql import functions as F

dedup = (df_oct.groupBy("product_id", "user_id")
           .agg(
               F.max("event_time").alias("event_time"),
               F.first("category_code", ignorenulls=True).alias("category_code")
           ))

display(dedup)

product_id user_id event_time category_code 1004873 555462013 2019-10-01T02:19:05.000Z electronics.smartphone 24900125 538034449 2019-10-01T02:20:53.000Z null 7005751 554001003 2019-10-01T02:26:01.000Z kids.carriage 12715582 513330295 2019-10-01T02:30:44.000Z null 1004259 542819113 2019-10-01T02:31:12.000Z electronics.smartphone 1004846 555463796 2019-10-01T02:32:17.000Z electronics.smartphone 12718925 517395416 2019-10-01T02:34:37.000Z null 47900002 514990478 2019-10-01T02:35:19.000Z null 43900051 527923014 2019-10-01T02:37:39.000Z null 42900004 512852948 2019-10-01T02:40:29.000Z construction.tools.light 9001887 515045254 2019-10-01T02:42:03.000Z kids.toys 17200778 545643568 2019-10-01T02:53:51.000Z furniture.living_room.sofa 1004428 516520908 2019-10-01T02:50:07.000Z electronics.smartphone 5300004 551631815 2019-10-01T02:52:26.000Z null 1003306 514186815 2019-10-04T06:04:02.000Z electronics.smartphone 4804056 522421166 2019-10-02T16:05:12.000Z electronics.audio.headphone 5100721 544000492 2019-10-01T02:55:10.000Z electronics.clocks 13300009 548584571 2019-10-01T02:55:40.000Z null 1004916 524152761 2019-10-01T02:58:22.000Z electronics.smartphone 2702001 532611026 2019-10-01T02:58:49.000Z appliances.kitchen.refrigerators 4804295 543815181 2019-10-31T07:46:44.000Z electronics.audio.headphone 26400629 539158469 2019-10-01T03:01:15.000Z null 28100343 541113258 2019-10-01T03:03:52.000Z null 28300595 538078498 2019-10-01T03:05:08.000Z accessories.wallet 1004794 555465399 2019-10-01T03:07:26.000Z electronics.smartphone 17800202 513036464 2019-10-01T03:11:35.000Z computers.desktop 1003306 528126136 2019-10-01T03:20:39.000Z electronics.smartphone 5000487 512905043 2019-10-01T03:23:40.000Z appliances.sewing_machine 34700079 524545944 2019-10-01T10:09:15.000Z null 1004460 517996859 2019-10-01T03:24:00.000Z electronics.smartphone 1004249 516429824 2019-10-26T17:22:59.000Z electronics.smartphone 1701421 515366261 2019-10-01T03:24:26.000Z computers.peripherals.monitor 14700144 533151611 2019-10-01T03:25:10.000Z furniture.living_room.cabinet 5100816 553351604 2019-10-07T10:17:06.000Z null 42000051 512723354 2019-10-01T03:30:51.000Z null 3701311 555470042 2019-10-01T03:36:37.000Z appliances.environment.vacuum 6200687 555469937 2019-10-01T03:33:39.000Z appliances.environment.air_heater 6200515 555469937 2019-10-01T03:35:24.000Z appliances.environment.air_heater 1004768 555473335 2019-10-01T03:37:47.000Z electronics.smartphone 1005159 512756464 2019-10-13T05:44:38.000Z electronics.smartphone 3500032 555473703 2019-10-01T03:43:46.000Z null 1004767 555475470 2019-10-01T03:44:06.000Z electronics.smartphone 19200081 537424879 2019-10-01T03:47:00.000Z construction.tools.saw 3701155 555476150 2019-10-01T03:47:18.000Z appliances.environment.vacuum 15800118 537173950 2019-10-01T03:47:33.000Z null 5100405 519574851 2019-10-01T03:55:41.000Z electronics.clocks 16000360 514925645 2019-10-01T03:52:48.000Z null 4300375 512408255 2019-10-01T03:54:00.000Z null 1003709 518895065 2019-10-06T14:52:43.000Z electronics.smartphone 9600061 513258834 2019-10-01T03:56:34.000Z null 4802036 541404186 2019-10-01T03:57:27.000Z electronics.audio.headphone 12719823 539511804 2019-10-01T03:59:29.000Z null 1004166 514421794 2019-10-01T04:02:45.000Z electronics.smartphone 4804056 514488912 2019-10-01T04:05:17.000Z electronics.audio.headphone 22700119 515551762 2019-10-01T04:08:07.000Z null 2900514 541693096 2019-10-01T04:09:13.000Z appliances.kitchen.microwave 12400045 518522957 2019-10-01T04:10:49.000Z construction.tools.drill 1306256 532599006 2019-10-01T04:13:19.000Z computers.notebook 12710449 519043534 2019-10-01T04:12:58.000Z null 1002536 555480341 2019-10-01T04:14:51.000Z electronics.smartphone 5701135 514514655 2019-10-01T04:16:31.000Z auto.accessories.player 3900774 515616020 2019-10-04T13:19:02.000Z appliances.environment.water_heater 32801022 517110814 2019-10-01T04:18:01.000Z null 12706655 555481020 2019-10-01T04:18:50.000Z null 1480334 542167762 2019-10-01T04:20:1